In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from pathlib import Path

try:
    from google.colab import drive

    drive.mount("/content/drive")
    workding_dir = "/content/drive/MyDrive/logical-reasoning/"
except ModuleNotFoundError:
    workding_dir = str(Path.cwd().parent)

In [3]:
import os
import sys
from pathlib import Path

os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /Users/inflaton/code/engd/projects/logical-reasoning


In [4]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /Users/inflaton/code/engd/projects/logical-reasoning/.env


True

In [5]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("LOGICAL_REASONING_DATA_PATH")
results_path = os.getenv("LOGICAL_REASONING_RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"

print(model_name, adapter_name_or_path, load_in_4bit, data_path, results_path)

internlm/internlm2_5-7b-chat-1m llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full/checkpoint-88 False datasets/mgtv results/mgtv-results_m3.csv


In [6]:
%%time
!python --version
!pip show flash-attn

Python 3.11.9
CPU times: user 4.51 ms, sys: 7.82 ms, total: 12.3 ms
Wall time: 652 ms


In [7]:
from llm_toolkit.llm_utils import *
from llm_toolkit.logical_reasoning_utils import *

device = check_gpu()

loading /Users/inflaton/code/engd/projects/logical-reasoning/llm_toolkit/logical_reasoning_utils.py
MPS is available


In [8]:
%%time

# model, tokenizer = load_model(model_name, adapter_name_or_path=adapter_name_or_path, using_llama_factory=False)
model, tokenizer = load_model(adapter_name_or_path, using_llama_factory=False)

loading model: llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full/checkpoint-88 with adapter: None


Loading checkpoint shards:   0%|          | 0/8 [00:00<?, ?it/s]

CPU times: user 2.49 s, sys: 5.85 s, total: 8.34 s
Wall time: 27.5 s


In [9]:
model.push_to_hub("inflaton-ai/InternLM_2_5-7b_LoRA-Adapter")

/Users/inflaton/anaconda3/envs/logical-reasoning/lib/python3.11/site-packages/transformers/integrations/peft.py:399: FutureWarning: The `active_adapter` method is deprecated and will be removed in a future version.
  warnings.warn(


adapter_model.safetensors:   0%|          | 0.00/37.8M [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/inflaton-ai/InternLM_2_5-7b_LoRA-Adapter/commit/822b89e129372ed5bc8372489ff6dcfef7d19cd7', commit_message='Upload InternLM2ForCausalLM', commit_description='', oid='822b89e129372ed5bc8372489ff6dcfef7d19cd7', pr_url=None, pr_revision=None, pr_num=None)

In [10]:
del model, tokenizer

In [12]:
%%time

model, tokenizer = load_model(model_name, adapter_name_or_path="inflaton-ai/InternLM_2_5-7b_LoRA-Adapter", using_llama_factory=False)
# model, tokenizer = load_model("inflaton-ai/InternLM_2_5-7b_LoRA-Adapter", using_llama_factory=False)

loading model: internlm/internlm2_5-7b-chat-1m with adapter: inflaton-ai/InternLM_2_5-7b_LoRA-Adapter


Loading checkpoint shards:   0%|          | 0/8 [00:00<?, ?it/s]

adapter_config.json:   0%|          | 0.00/679 [00:00<?, ?B/s]

adapter_model.safetensors:   0%|          | 0.00/37.8M [00:00<?, ?B/s]

CPU times: user 3.06 s, sys: 5.04 s, total: 8.11 s
Wall time: 31.6 s


In [13]:
datasets = load_logical_reasoning_dataset(
    data_path,
    tokenizer=tokenizer,
    chinese_prompt=not use_english_datasets,
    using_p1=False,
)

loading train/test data files


Map:   0%|          | 0/25000 [00:00<?, ? examples/s]

Map:   0%|          | 0/3000 [00:00<?, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth', 'train_text', 'prompt'],
        num_rows: 25000
    })
    test: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth', 'train_text', 'prompt'],
        num_rows: 3000
    })
})


In [14]:
%%time

prompt1 = datasets["test"]["prompt"][1000]

gen_kwargs = {"max_length": 4096, "do_sample": True, "top_k": 1}
with torch.no_grad():
    inputs = tokenizer(
        [prompt1],
        return_tensors="pt",
    ).to(device)
    outputs = model.generate(**inputs, **gen_kwargs)
    outputs = outputs[:, inputs['input_ids'].shape[1]:]
    print(tokenizer.decode(outputs[0], skip_special_tokens=True))

/Users/inflaton/anaconda3/envs/logical-reasoning/lib/python3.11/site-packages/transformers/generation/utils.py:1513: UserWarning: The operator 'aten::isin.Tensor_Tensor_out' is not currently supported on the MPS backend and will fall back to run on the CPU. This may have performance implications. (Triggered internally at /Users/runner/work/pytorch/pytorch/pytorch/aten/src/ATen/mps/MPSFallback.mm:13.)
  if eos_token_id is not None and torch.isin(elements=eos_token_id, test_elements=pad_token_id).any():


是
CPU times: user 579 ms, sys: 330 ms, total: 909 ms
Wall time: 2.86 s
